<a href="https://colab.research.google.com/github/JohnPaul1278/PS0/blob/main/therealps3.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import time, os, sys, re
import zipfile, json, datetime, string
import numpy as np
from statistics import *

import matplotlib.pyplot as plt

import pandas as pd
import pandas_datareader as pdr
from pandas_datareader import wb
from pandas.io.formats.style import Styler


from google.colab import files

import seaborn as sns

from google.colab import data_table
data_table.enable_dataframe_formatter()

from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"

%matplotlib inline

plt.style.use('classic')

aok: no!!! need to download first with wget!!!!!

In [21]:
!wget -q -O freedom.xlsx  https://github.com/JohnPaul1278/ps3/raw/main/freedom.xlsx
!wget -q -O econfree.csv  https://github.com/JohnPaul1278/ps3/raw/main/econfree.csv
!wget -q -O depression.csv  https://github.com/JohnPaul1278/ps3/raw/main/depressive-disorders-prevalence-ihme.csv #not sure if thats the one you want


In [4]:
freedom = pd.ExcelFile('freedom.xlsx') #there are two sheets in this file but I only need one of them. I found this solution to define each separately.
df1 = pd.read_excel('freedom.xlsx', 'Index') #I don't think I'll need this in the merge itself
df2 = pd.read_excel('freedom.xlsx', 'FIW13-23') #THIS is the important one. This is the freedom index from Freedom House.

#here is the link to where I found this data: https://freedomhouse.org/report/freedom-world

#I don't anticipate using all of the data in this file. It's huge.
#I think I'll probably use data from specific years and countries based on what my other datasets have.
#I also don't know if I'll be looking at every type of freedom that is documented here. Some will be more interesting to compare than others.
#also the formatting is pretty frustrating so I think I'll rename all the unnamed variables.

df2

Freedom in the World 2013-2023 Raw Data   Unnamed: 1 Unnamed: 2  \
0                          Country/Territory       Region        C/T   
1                                   Abkhazia      Eurasia          t   
2                                Afghanistan         Asia          c   
3                                    Albania       Europe          c   
4                                    Algeria       Africa          c   
...                                      ...          ...        ...   
2301                               West Bank  Middle East          t   
2302                          Western Sahara       Africa          t   
2303                                   Yemen  Middle East          c   
2304                                  Zambia       Africa          c   
2305                                Zimbabwe       Africa          c   

     Unnamed: 3 Unnamed: 4 Unnamed: 5 Unnamed: 6 Unnamed: 7 Unnamed: 8  \
0       Edition     Status  PR rating  CL rating         A1         A2   
1          2023         PF          5          5          2          2   
2          2023         NF          7          7          0          0   
3          2023         PF          3          3          3          3   
4          2023         NF          6          5          1          1   
...         ...        ...        ...        ...        ...        ...   
2301       2013         NF          6          5          0          0   
2302       2013         NF          7          7          0          0   
2303       2013         NF          6          6          1          0   
2304       2013         PF          3          4          3          3   
2305       2013         NF          6          6          1          1   

     Unnamed: 9  ... Unnamed: 34 Unnamed: 35 Unnamed: 36 Unnamed: 37  \
0            A3  ...          F3          F4           F          G1   
1             1  ...           1           1           4           1   
2             0  ...           0           0           0           0   
3             3  ...           2           3           9           3   
4             1  ...           2           2           6           2   
...         ...  ...         ...         ...         ...         ...   
2301          2  ...           0           1           5           1   
2302          0  ...           0           0           0           1   
2303          2  ...           0           1           2           2   
2304          3  ...           2           2           8           3   
2305          1  ...           0           0           1           1   

     Unnamed: 38 Unnamed: 39 Unnamed: 40 Unnamed: 41 Unnamed: 42 Unnamed: 43  
0             G2          G3          G4           G          CL       Total  
1              1           2           1           5          22          39  
2              1           0           1           2           7           8  
3              2           2           2           9          39          67  
4              2           2           1           7          22          32  
...          ...         ...         ...         ...         ...         ...  
2301           1           2           1           5          24          30  
2302           1           2           0           4           7           5  
2303           1           1           1           5          16          25  
2304           2           1           2           8          34          62  
2305           1           1           1           4          14          25  

[2306 rows x 44 columns]

In [10]:
df2 = df2.rename(columns={'Unnamed: 3': 'year',  #easier to see if you spread over multiple rows
                          'Unnamed: 4': 'Status',
                          'Unnamed: 5': 'PoliticalRights', 'Unnamed: 6': 'CivilLiberties', 'Freedom in the World 2013-2023 Raw Data': 'Countries' })
df3 = df2[df2.year == 2021] #I decided to look at 2021 specifically because it matches the year of my second dataset. It also just cleans up the otherwise massive file.
df3 = df3[['Countries', 'year', 'Status', 'PoliticalRights', 'CivilLiberties']] #the subcategories are interesting, but I can go back to the original file if I want to look at them
#for now I'm cutting the subcategories like "individual freedoms" and "right to assembly" and I'm just looking at Political Rights and Civil Liberties
#I'm also looking at "status," which ranges from (F)ree, (P)artially (F)ree, and (N)ot (F)ree
df3

Countries  year Status PoliticalRights CivilLiberties
421        Abkhazia  2021     PF               5              5
422     Afghanistan  2021     NF               5              6
423         Albania  2021     PF               3              3
424         Algeria  2021     NF               6              5
425         Andorra  2021      F               1              1
..              ...   ...    ...             ...            ...
626       West Bank  2021     NF               7              5
627  Western Sahara  2021     NF               7              7
628           Yemen  2021     NF               7              6
629          Zambia  2021     PF               4              4
630        Zimbabwe  2021     NF               6              5

[210 rows x 5 columns]

aok thats fine to use code cells like below with comments; but note can also text cells like this one :)

In [7]:
econfree=pd.read_csv('econfree.csv') #here is my second dataset. This is an economic freedom index from a different institution
#the slight change in perspective is interesting. I think many of the same questions are asked but the small differences between the two datasets may reveal something interesting
#here is where I found the dataset: https://www.fraserinstitute.org/economic-freedom/dataset?geozone=world&page=dataset&min-year=2&max-year=0&filter=0
econfree #one again there are many, many variables. This time around the only year is 2021, at least.
#the formatting for this is even worse than the last one. I'm going to cut most of this
#I don't mean to dismiss the importance of the other factors, but I'm cutting everything apart from the main variable for now
#the main variable, Economic Freedom Summary Index, is what I want to compare to data from other countries.
#If I find interesting connections between EFSI and other datasets I can always come back to the original file to look at the subcategories later.

Unnamed: 0 Unnamed: 1 Unnamed: 2    Unnamed: 3  \
0           NaN        NaN        NaN           NaN   
1           NaN        NaN        NaN           NaN   
2           NaN        NaN        NaN           NaN   
3           NaN       Year   ISO Code     Countries   
4           NaN       2021        AGO        Angola   
..          ...        ...        ...           ...   
164         NaN       2021        VNM       Vietnam   
165         NaN       2021        YEM   Yemen, Rep.   
166         NaN       2021        ZAF  South Africa   
167         NaN       2021        ZMB        Zambia   
168         NaN       2021        ZWE      Zimbabwe   

                         Unnamed: 4 Unnamed: 5 Unnamed: 6  \
0                               NaN        NaN        NaN   
1                               NaN        NaN        NaN   
2                               NaN        NaN        NaN   
3    Economic Freedom Summary Index       Rank   Quartile   
4                              5.38        149          4   
..                              ...        ...        ...   
164                            6.26        106          3   
165                            4.18        161          4   
166                            6.53         94          3   
167                            5.84        129          4   
168                            3.81        164          4   

                 Unnamed: 7 Unnamed: 8               Unnamed: 9  ...  \
0                    Area 1        NaN                      NaN  ...   
1                        1A        NaN                       1B  ...   
2                       NaN        NaN                      NaN  ...   
3    Government consumption       data  Transfers and subsidies  ...   
4                      7.18      15.59                     9.70  ...   
..                      ...        ...                      ...  ...   
164                    7.42      14.78                      NaN  ...   
165                    8.75      10.26                     9.02  ...   
166                    4.66      24.16                     7.87  ...   
167                    1.68      34.28                     9.32  ...   
168                    6.89      16.58                     8.50  ...   

           Unnamed: 67       Unnamed: 68                      Unnamed: 69  \
0                  NaN               NaN                              NaN   
1                   5C               NaN                              NaN   
2                  5Ci              5Cii                            5Ciii   
3    Regulatory Burden  Bureacracy costs  Impartial Public Administration   
4                 2.94              4.67                             4.90   
..                 ...               ...                              ...   
164               3.98              5.56                             3.88   
165               2.94              0.00                             0.62   
166               3.36              4.22                             6.34   
167               4.22              3.33                             4.39   
168               2.41              2.67                             2.63   

        Unnamed: 70           Unnamed: 71      Unnamed: 72       Unnamed: 73  \
0               NaN                   NaN              NaN               NaN   
1               NaN                   NaN               5D               NaN   
2              5Civ                   NaN              5Di              5Dii   
3    Tax compliance  Business regulations  Market openness  Business Permits   
4              4.64                  4.29             3.10              7.92   
..              ...                   ...              ...               ...   
164            4.79                  4.55             4.55              8.21   
165            6.11                  2.42             2.07               NaN   
166            7.57                  5.37             5.30              8.39   
167            4.30  

In [8]:
econfree = econfree.rename(columns={'Unnamed: 1': 'year', 'Unnamed: 3': 'countries', 'Unnamed: 4': 'efsi'}) #once again we need to rename things
econfree = econfree.rename(columns= {'countries': 'Countries'}) #I tried to change it without adding another row but it didn't work for some reason
econfree = econfree[['year', 'Countries', 'efsi']]
econfree = econfree[4::]#the top three rows were useless. They seemed to be organizing tools for the researchers who compiled the data
#I don't think I could have used anything from the top three rows
#plus this is much prettier!
econfree

year             Countries  efsi
4    2021                Angola  5.38
5    2021               Albania  7.60
6    2021  United Arab Emirates  7.35
7    2021             Argentina  4.77
8    2021               Armenia  7.58
..    ...                   ...   ...
164  2021               Vietnam  6.26
165  2021           Yemen, Rep.  4.18
166  2021          South Africa  6.53
167  2021                Zambia  5.84
168  2021              Zimbabwe  3.81

[165 rows x 3 columns]

In [11]:
merge1 = pd.merge(df3, econfree, how='outer', on='Countries', indicator=True) #aok: always investigate!!!
#sort on _merge
#see for instance bahamas didnt merge right

# so need to replace on condition like this:
#auto.loc[auto['foreign'] =='Domestic', 'colOfOnes']  = '100'

#if I made any graphs from this I would include "2021" in the title.
merge1

Countries year_x Status PoliticalRights CivilLiberties year_y  \
0                Abkhazia   2021     PF               5              5    NaN   
1             Afghanistan   2021     NF               5              6    NaN   
2                 Albania   2021     PF               3              3   2021   
3                 Algeria   2021     NF               6              5   2021   
4                 Andorra   2021      F               1              1    NaN   
..                    ...    ...    ...             ...            ...    ...   
224       Slovak Republic    NaN    NaN             NaN            NaN   2021   
225  Syrian Arab Republic    NaN    NaN             NaN            NaN   2021   
226               Türkiye    NaN    NaN             NaN            NaN   2021   
227         Venezuela, RB    NaN    NaN             NaN            NaN   2021   
228           Yemen, Rep.    NaN    NaN             NaN            NaN   2021   

     efsi      _merge  
0     NaN   left_only  
1     NaN   left_only  
2    7.60        both  
3    4.82        both  
4     NaN   left_only  
..    ...         ...  
224  7.49  right_only  
225  3.90  right_only  
226  6.32  right_only  
227  3.01  right_only  
228  4.18  right_only  

[229 rows x 8 columns]

# have sections
## and subsections like this

In [22]:
depression= pd.read_csv('depression.csv')
depression #this data only goes to 2019, whereas my earlier two datasets looked at data from 2021
#that's not ideal. The COVID pandemic almost certainly impacted the levels of depressive disorders in every country
#I'm using it anyway for the sake of the assignment, but everything I do with this dataset should have a big asterix next to it.

Entity Code  Year  \
0     Afghanistan  AFG  1990   
1     Afghanistan  AFG  1991   
2     Afghanistan  AFG  1992   
3     Afghanistan  AFG  1993   
4     Afghanistan  AFG  1994   
...           ...  ...   ...   
6415     Zimbabwe  ZWE  2015   
6416     Zimbabwe  ZWE  2016   
6417     Zimbabwe  ZWE  2017   
6418     Zimbabwe  ZWE  2018   
6419     Zimbabwe  ZWE  2019   

      Depressive disorders (share of population) - Sex: Both - Age: Age-standardized  
0                                              4.996118                               
1                                              4.989290                               
2                                              4.981346                               
3                                              4.976958                               
4                                              4.977782                               
...                                                 ...                               
6415                                           3.407624                               
6416                                           3.410755                               
6417                                           3.411965                               
6418                                           3.406929                               
6419                                           3.395476                               

[6420 rows x 4 columns]

In [23]:
depression= depression[depression.Year==2017]
depression #and there we go. Obviously a comparison of datasets that all come from the same year would be better, but this is far from useless.
#we can see how depression interacted or did not interact with political freedom, civil liberties, and economic freedom before the pandemic
#our biggest assumption here is that freedom stayed roughly the same from 2017 to 2021
#antivaxxers might disagree but fuck 'em lol
#don't penalize me for that it was funny
#anyway, this dataset and the first dataset both have data for many years, so we could always compare them without using the econfree dataset
#but for the sake of the assignment I'm proceeding as is.


Entity      Code  Year  \
27           Afghanistan       AFG  2017   
57     Africa (IHME GBD)       NaN  2017   
87               Albania       ALB  2017   
117              Algeria       DZA  2017   
147   America (IHME GBD)       NaN  2017   
...                  ...       ...   ...   
6297             Vietnam       VNM  2017   
6327               World  OWID_WRL  2017   
6357               Yemen       YEM  2017   
6387              Zambia       ZMB  2017   
6417            Zimbabwe       ZWE  2017   

      Depressive disorders (share of population) - Sex: Both - Age: Age-standardized  
27                                             4.930936                               
57                                             4.453067                               
87                                             2.443582                               
117                                            4.064613                               
147                                            3.604466                               
...                                                 ...                               
6297                                           2.472004                               
6327                                           3.433322                               
6357                                           4.874499                               
6387                                           4.213495                               
6417                                           3.411965                               

[214 rows x 4 columns]

In [24]:
depression= depression.rename(columns={'Entity': 'Countries', #again easier to see like this
                                       'Depressive disorders (share of population) - Sex: Both - Age: Age-standardized': 'Depression (%)'})
depression= depression[['Countries', 'Depression (%)']]
#I know the depressive disorder label is long, but I appreciate the information it conveys. I might change it later if it keeps being annoying.
#I'm keeping it for now so I can tell what the numbers mean.
depression

Countries  Depression (%)
27           Afghanistan        4.930936
57     Africa (IHME GBD)        4.453067
87               Albania        2.443582
117              Algeria        4.064613
147   America (IHME GBD)        3.604466
...                  ...             ...
6297             Vietnam        2.472004
6327               World        3.433322
6357               Yemen        4.874499
6387              Zambia        4.213495
6417            Zimbabwe        3.411965

[214 rows x 2 columns]

In [26]:
del merge1['_merge']

In [27]:
merge2 = pd.merge(merge1, depression, how='outer', on='Countries', indicator=True) #again most stuff didnt merge! fix it!!
merge2 #the economic freedom dataset doesn't include a number of these countries.
#the depression dataset and the freedom dataset also include a large number of territories and other entities that aren't technically countries.
#while it would be cleaner to get rid of some of these, I want to keep everything for now in case we can infer something interesting from the gap in data collection from certain organizations

Countries year_x Status PoliticalRights  \
0                            Abkhazia   2021     PF               5   
1                         Afghanistan   2021     NF               5   
2                             Albania   2021     PF               3   
3                             Algeria   2021     NF               6   
4                             Andorra   2021      F               1   
..                                ...    ...    ...             ...   
254  Saint Vincent and the Grenadines    NaN    NaN             NaN   
255                           Tokelau    NaN    NaN             NaN   
256      United States Virgin Islands    NaN    NaN             NaN   
257     Upper-middle-income countries    NaN    NaN             NaN   
258                             World    NaN    NaN             NaN   

    CivilLiberties year_y  efsi  Depression (%)      _merge  
0                5    NaN   NaN             NaN   left_only  
1                6    NaN   NaN        4.930936        both  
2                3   2021  7.60        2.443582        both  
3                5   2021  4.82        4.064613        both  
4                1    NaN   NaN        3.560528        both  
..             ...    ...   ...             ...         ...  
254            NaN    NaN   NaN        3.301090  right_only  
255            NaN    NaN   NaN        3.120299  right_only  
256            NaN    NaN   NaN        3.298711  right_only  
257            NaN    NaN   NaN        3.134088  right_only  
258            NaN    NaN   NaN        3.433322  right_only  

[259 rows x 9 columns]

In [ ]:
prison= pd.read_csv('incarceration.csv')
prison #okay, this one is pretty fun to compare to the freedom index dataset, but I'm also interested in how it compares with the econ and depression sets
#I'm definitely going to have to rename these. These names are awful.
#this dataset is from 2023, but the data itself is from 2021
#"per data released in October 2021 by World Prison Brief"
#Here's where I found it: https://worldpopulationreview.com/country-rankings/incarceration-rates-by-country


country  incarcerationRatesByCountry_ratePer100k  \
0               United States                                      629   
1                      Rwanda                                      580   
2                Turkmenistan                                      576   
3                 El Salvador                                      564   
4                        Cuba                                      510   
..                        ...                                      ...   
212     Republic of the Congo                                       27   
213                    Gambia                                       23   
214             Faroe Islands                                       18   
215  Central African Republic                                       16   
216                San Marino                                        0   

     incarcerationRatesByCountry_totIncarcerated  \
0                                        2068800   
1                                          76099   
2                                          35000   
3                                          36663   
4                                          57337   
..                                           ...   
212                                         1388   
213                                          543   
214                                            9   
215                                          764   
216                                            0   

     incarcerationRatesByCountry_percMale  \
0                                    0.90   
1                                    0.95   
2                                    0.94   
3                                    0.93   
4                                     NaN   
..                                    ...   
212                                  0.96   
213                                  0.98   
214                                  1.00   
215                                  0.97   
216                                  0.00   

     incarcerationRatesByCountry_percFemale  
0                                      0.10  
1                                      0.05  
2                                      0.07  
3                                      0.07  
4                                       NaN  
..                                      ...  
212                                    0.04  
213                                    0.03  
214                                    0.00  
215                                    0.03  
216                                    0.00  

[217 rows x 5 columns]

In [ ]:
prison=prison.rename (columns= {'country': 'Countries', 'incarcerationRatesByCountry_ratePer100k': 'Incarceration Rate', 'incarcerationRatesByCountry_totIncarcerated': 'Total Incarcerated'})
prison #as a reminder to myself and a note to you: the incarceration rate refers to the number of people imprisoned per 100k.
#in the US, for example, there are 629 incarcerated individuals for every 100k people.

Countries  Incarceration Rate  Total Incarcerated  \
0               United States                 629             2068800   
1                      Rwanda                 580               76099   
2                Turkmenistan                 576               35000   
3                 El Salvador                 564               36663   
4                        Cuba                 510               57337   
..                        ...                 ...                 ...   
212     Republic of the Congo                  27                1388   
213                    Gambia                  23                 543   
214             Faroe Islands                  18                   9   
215  Central African Republic                  16                 764   
216                San Marino                   0                   0   

     incarcerationRatesByCountry_percMale  \
0                                    0.90   
1                                    0.95   
2                                    0.94   
3                                    0.93   
4                                     NaN   
..                                    ...   
212                                  0.96   
213                                  0.98   
214                                  1.00   
215                                  0.97   
216                                  0.00   

     incarcerationRatesByCountry_percFemale  
0                                      0.10  
1                                      0.05  
2                                      0.07  
3                                      0.07  
4                                       NaN  
..                                      ...  
212                                    0.04  
213                                    0.03  
214                                    0.00  
215                                    0.03  
216                                    0.00  

[217 rows x 5 columns]

In [ ]:
prison=prison[['Countries', 'Incarceration Rate', 'Total Incarcerated']]
prison #the gender data is interesting, don't get me wrong, but as in the other cases, I can always come back to the original file if I have to
#for now I'm interested in looking at fairly broad trends between sets
#and I don't need subcategory variables all over the place

Countries  Incarceration Rate  Total Incarcerated
0               United States                 629             2068800
1                      Rwanda                 580               76099
2                Turkmenistan                 576               35000
3                 El Salvador                 564               36663
4                        Cuba                 510               57337
..                        ...                 ...                 ...
212     Republic of the Congo                  27                1388
213                    Gambia                  23                 543
214             Faroe Islands                  18                   9
215  Central African Republic                  16                 764
216                San Marino                   0                   0

[217 rows x 3 columns]

In [ ]:
merge3 = pd.merge(merge2, prison, how='outer', on='Countries')
merge3 #Once I have more merges complete I will sift through all the NaNs and see if I can simplify further. For now I'm keeping it.
#the incarceration rate is somewhat high for quite a few so-called "free" countries. The United States is the most glaring example, but others exist.
#Look at Argentina and Brazil, for example: while their incarceration rates are less than half than that of the US, they still have many people incarcerated
#this might be interesting to consider in light of the "developed"/"developing" terminology often used in the social sciences.
#whatever else may need "developing," the prison systems in these countries has clearly been "developed" already.
#the most depressed countries vary wildly in terms of their incarceration rates.
#the Central African Republic has many depressed people but very few people in prison.
#this might be a better example of a country with a prison system or justicial system that is still "developing"
#that's just one explanation, of course.

Countries Status PoliticalRights CivilLiberties  efsi  \
0                 Abkhazia     PF               5              5   NaN   
1              Afghanistan     NF               5              6   NaN   
2                  Albania     PF               3              3  7.60   
3                  Algeria     NF               6              5  4.82   
4                  Andorra      F               1              1   NaN   
..                     ...    ...             ...            ...   ...   
275               Guernsey    NaN             NaN            NaN   NaN   
276            Ivory Coast    NaN             NaN            NaN   NaN   
277               DR Congo    NaN             NaN            NaN   NaN   
278  Republic of the Congo    NaN             NaN            NaN   NaN   
279          Faroe Islands    NaN             NaN            NaN   NaN   

     Depressive disorders (share of population) - Sex: Both - Age: Age-standardized  \
0                                                  NaN                                
1                                             4.945168                                
2                                             2.460203                                
3                                             4.129681                                
4                                             3.607207                                
..                                                 ...                                
275                                                NaN                                
276                                                NaN                                
277                                                NaN                                
278                                                NaN                                
279                                                NaN                                

     Incarceration Rate  Total Incarcerated  
0                   NaN                 NaN  
1                  77.0             28240.0  
2                 179.0              5042.0  
3                 153.0             65000.0  
4                  78.0                61.0  
..                  ...                 ...  
275               124.0                82.0  
276                82.0             21430.0  
277                29.0             20550.0  
278                27.0              1388.0  
279                18.0                 9.0  

[280 rows x 8 columns]

In [ ]:
fish=pd.read_csv('fish.csv')
fish
#sometimes you gotta get weird
#what if fish consumption correlates with freedom???
#what if fish consumption correlates with incarceration???

Entity Code  Year  \
0      Afghanistan  AFG  1961   
1      Afghanistan  AFG  1962   
2      Afghanistan  AFG  1963   
3      Afghanistan  AFG  1964   
4      Afghanistan  AFG  1965   
...            ...  ...   ...   
12355     Zimbabwe  ZWE  2016   
12356     Zimbabwe  ZWE  2017   
12357     Zimbabwe  ZWE  2018   
12358     Zimbabwe  ZWE  2019   
12359     Zimbabwe  ZWE  2020   

       Fish and seafood | 00002960 || Food available for consumption | 0645pc || kilograms per year per capita  
0                                               0.030559                                                        
1                                               0.030578                                                        
2                                               0.030598                                                        
3                                               0.030614                                                        
4                                               0.030627                                                        
...                                                  ...                                                        
12355                                           3.679239                                                        
12356                                           3.397224                                                        
12357                                           3.117559                                                        
12358                                           2.870986                                                        
12359                                           2.817092                                                        

[12360 rows x 4 columns]

In [ ]:
fish= fish[fish.Year==2017]
fish= fish.rename(columns ={'Entity': 'Countries'})
fish

Countries      Code  Year  \
56              Afghanistan       AFG  2017   
116                  Africa       NaN  2017   
176            Africa (FAO)       NaN  2017   
236                 Albania       ALB  2017   
296                 Algeria       DZA  2017   
...                     ...       ...   ...   
12085  Western Europe (FAO)       NaN  2017   
12145                 World  OWID_WRL  2017   
12205                 Yemen       YEM  2017   
12296                Zambia       ZMB  2017   
12356              Zimbabwe       ZWE  2017   

       Fish and seafood | 00002960 || Food available for consumption | 0645pc || kilograms per year per capita  
56                                              0.254577                                                        
116                                             9.964374                                                        
176                                            10.120000                                                        
236                                             8.643904                                                        
296                                             3.883688                                                        
...                                                  ...                                                        
12085                                          21.510000                                                        
12145                                          20.047707                                                        
12205                                           2.937864                                                        
12296                                          11.740666                                                        
12356                                           3.397224                                                        

[222 rows x 4 columns]

In [ ]:
mergefish = pd.merge(merge3, fish, how='outer', on='Countries')
mergefish
#the world will forever be in my debt for this contribution to science.
#you're welcome.

Countries Status PoliticalRights CivilLiberties  efsi  \
0                 Abkhazia     PF               5              5   NaN   
1              Afghanistan     NF               5              6   NaN   
2                  Albania     PF               3              3  7.60   
3                  Algeria     NF               6              5  4.82   
4                  Andorra      F               1              1   NaN   
..                     ...    ...             ...            ...   ...   
313    Southern Asia (FAO)    NaN             NaN            NaN   NaN   
314  Southern Europe (FAO)    NaN             NaN            NaN   NaN   
315   Western Africa (FAO)    NaN             NaN            NaN   NaN   
316     Western Asia (FAO)    NaN             NaN            NaN   NaN   
317   Western Europe (FAO)    NaN             NaN            NaN   NaN   

     Depressive disorders (share of population) - Sex: Both - Age: Age-standardized  \
0                                                  NaN                                
1                                             4.945168                                
2                                             2.460203                                
3                                             4.129681                                
4                                             3.607207                                
..                                                 ...                                
313                                                NaN                                
314                                                NaN                                
315                                                NaN                                
316                                                NaN                                
317                                                NaN                                

     Incarceration Rate  Total Incarcerated Code    Year  \
0                   NaN                 NaN  NaN     NaN   
1                  77.0             28240.0  AFG  2017.0   
2                 179.0              5042.0  ALB  2017.0   
3                 153.0             65000.0  DZA  2017.0   
4                  78.0                61.0  NaN     NaN   
..                  ...                 ...  ...     ...   
313                 NaN                 NaN  NaN  2017.0   
314                 NaN                 NaN  NaN  2017.0   
315                 NaN                 NaN  NaN  2017.0   
316                 NaN                 NaN  NaN  2017.0   
317                 NaN                 NaN  NaN  2017.0   

     Fish and seafood | 00002960 || Food available for consumption | 0645pc || kilograms per year per capita  
0                                                  NaN                                                        
1                                             0.254577                                                        
2                                             8.643904                                                        
3                                             3.883688                                                        
4                                                  NaN                                                        
..                                                 ...                                                        
313                                           8.270000                                                        
314                                          31.550000                                                        
315                                          11.860000                                                        
316                                           7.520000                                                        
317                                          21.510000                                                        

[318 rows x 11 columns]

In [ ]:
depression2= pd.read_csv('depression.csv')
depression2= depression2[(depression2.Year==2016)| (depression2.Year==2015)]
depression2= depression2.rename(columns={'Year': 'year'})
depression2


Entity Code  year  \
25          Afghanistan  AFG  2015   
26          Afghanistan  AFG  2016   
55    Africa (IHME GBD)  NaN  2015   
56    Africa (IHME GBD)  NaN  2016   
85              Albania  ALB  2015   
...                 ...  ...   ...   
6356              Yemen  YEM  2016   
6385             Zambia  ZMB  2015   
6386             Zambia  ZMB  2016   
6415           Zimbabwe  ZWE  2015   
6416           Zimbabwe  ZWE  2016   

      Depressive disorders (share of population) - Sex: Both - Age: Age-standardized  
25                                             4.944759                               
26                                             4.937072                               
55                                             4.443779                               
56                                             4.448507                               
85                                             2.442234                               
...                                                 ...                               
6356                                           4.884568                               
6385                                           4.197497                               
6386                                           4.206809                               
6415                                           3.407624                               
6416                                           3.410755                               

[428 rows x 4 columns]

In [ ]:
merge4= pd.merge(depression2, prison, left_on='Entity', right_on='Countries')
merge4 #we could use this data to see if incarceration rate correlates with depression.

Entity Code  year  \
0    Afghanistan  AFG  2015   
1    Afghanistan  AFG  2016   
2        Albania  ALB  2015   
3        Albania  ALB  2016   
4        Algeria  DZA  2015   
..           ...  ...   ...   
377        Yemen  YEM  2016   
378       Zambia  ZMB  2015   
379       Zambia  ZMB  2016   
380     Zimbabwe  ZWE  2015   
381     Zimbabwe  ZWE  2016   

     Depressive disorders (share of population) - Sex: Both - Age: Age-standardized  \
0                                             4.944759                                
1                                             4.937072                                
2                                             2.442234                                
3                                             2.441605                                
4                                             4.076484                                
..                                                 ...                                
377                                           4.884568                                
378                                           4.197497                                
379                                           4.206809                                
380                                           3.407624                                
381                                           3.410755                                

       Countries  Incarceration Rate  Total Incarcerated  
0    Afghanistan                  77               28240  
1    Afghanistan                  77               28240  
2        Albania                 179                5042  
3        Albania                 179                5042  
4        Algeria                 153               65000  
..           ...                 ...                 ...  
377        Yemen                  35                9719  
378       Zambia                 123               22823  
379       Zambia                 123               22823  
380     Zimbabwe                 115               20407  
381     Zimbabwe                 115               20407  

[382 rows x 7 columns]